In [2]:
import gradio as gr
from transformers.utils import logging
import time
import joblib
import re
import numpy as np

from src import get_lexical_desc,get_morphemic_desc, preprocess

logging.set_verbosity_info()
logger = logging.get_logger("transformers")

In [3]:
loaded_rf = joblib.load("rfc_30_0.95.joblib")
folders = ['eastern', 'western', 'grabar']

text='western - Աստուած ըսաւ. «Մեր պատկերով, մեր նմանութեան պէս մարդ ընենք, որ տիրապետէն ծովու ձուկերուն, երկինքի թռչուններուն եւ ընտանի անասուններուն, ամբողջ երկրին, ու երկրի վրայ ըսողացող բոլոր սողուններուն».* 27 Աստուած իր պատկերով ստեղծեց մարդը'


words=preprocess(text)
desc_lexical=get_lexical_desc(words).reshape((1,-1))
desc_morphemic=get_morphemic_desc(words).reshape((1,-1))


data=np.concatenate([desc_morphemic,desc_lexical],axis=1)

loaded_rf.predict_proba(data)[0]

[Parallel(n_jobs=1)]: Done  49 tasks      | elapsed:    0.0s


array([0.07140597, 0.85206542, 0.07652861])

In [5]:
def classify(input_text_message: str):

    logger.info(time.strftime("%Y.%m.%d, %H:%M:%S")+' '+'input text message: '+input_text_message)

    words=preprocess(input_text_message)
    desc_lexical=get_lexical_desc(words).reshape((1,-1))
    desc_morphemic=get_morphemic_desc(words).reshape((1,-1))
    
    data=np.concatenate([desc_morphemic,desc_lexical],axis=1)
    prediction=loaded_rf.predict_proba(data)[0]

    confidences = {labels[i]: float(prediction[i]) for i in range(3)}
    
    return confidences

labels = ['eastern armenian', 'western armenian', 'grabar (classic) armenian']

loaded_rf = joblib.load("rfc_30_0.95.joblib")

text='western - Աստուած ըսաւ. «Մեր պատկերով, մեր նմանութեան պէս մարդ ընենք, որ տիրապետէն ծովու ձուկերուն, երկինքի թռչուններուն եւ ընտանի անասուններուն, ամբողջ երկրին, ու երկրի վրայ ըսողացող բոլոր սողուններուն».* 27 Աստուած իր պատկերով ստեղծեց մարդը'

examples=[text]

with gr.Blocks() as demo:
    gr.Markdown("Check your text for compliance with the NVC rules")


    with gr.Tab("Single message analysis"):
        text_input = gr.Textbox(lines=2, placeholder="Enter your text here")
        text_button = gr.Button("Define dialect group")
        examples_block = gr.Examples(examples=examples,
                                     inputs=[text_input], )

        rec_output = gr.Label(label='Labels', num_top_classes=3)

        text_button.click(classify, inputs=text_input,
                          outputs=[rec_output])


demo.launch(share=True, debug=True)

Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://f0de872179e31656f7.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


2023.08.07, 01:06:33 input text message: western - Աստուած ըսաւ. «Մեր պատկերով, մեր նմանութեան պէս մարդ ընենք, որ տիրապետէն ծովու ձուկերուն, երկինքի թռչուններուն եւ ընտանի անասուններուն, ամբողջ երկրին, ու երկրի վրայ ըսողացող բոլոր սողուններուն».* 27 Աստուած իր պատկերով ստեղծեց մարդը
[Parallel(n_jobs=1)]: Done  49 tasks      | elapsed:    0.0s


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://f0de872179e31656f7.gradio.live
